In [1]:
%load_ext autoreload
%autoreload 2
import os
os.sys.path.insert(0, '/home/schirrmr/braindecode/code/braindecode/')

# Trialwise Decoding

In this example, we will use a convolutional neural network on the [Physiobank EEG Motor Movement/Imagery Dataset](https://www.physionet.org/physiobank/database/eegmmidb/) to decode two classes:

1. Executed and imagined opening and closing of both hands
2. Executed and imagined opening and closing of both feet

<div class="alert alert-warning">

We use only one subject (with 90 trials) in this tutorial for demonstration purposes. A more interesting decoding task with many more trials would be to do cross-subject decoding on the same dataset.

</div>

## Enable logging

In [2]:
import logging
import importlib
importlib.reload(logging) # see https://stackoverflow.com/a/21475297/1469195
log = logging.getLogger()
log.setLevel('INFO')
import sys

logging.basicConfig(format='%(asctime)s %(levelname)s : %(message)s',
                     level=logging.INFO, stream=sys.stdout)

## Load data

You can load and preprocess your EEG dataset in any way, Braindecode only expects a 3darray (trials, channels, timesteps) of input signals `X` and a vector of labels `y` later (see below). In this tutorial, we will use the [MNE](https://www.martinos.org/mne/stable/index.html) library to load an EEG motor imagery/motor execution dataset. For a tutorial from MNE using Common Spatial Patterns to decode this data, see [here](http://martinos.org/mne/stable/auto_examples/decoding/plot_decoding_csp_eeg.html). For another library useful for loading EEG data, take a look at [Neo IO](https://pythonhosted.org/neo/io.html).

In [3]:
import mne
from mne.io import concatenate_raws

# 5,6,7,10,13,14 are codes for executed and imagined hands/feet
subject_id = 22 # carefully cherry-picked to give nice results on such limited data :)
event_codes = [5,6,9,10,13,14]
#event_codes = [3,4,5,6,7,8,9,10,11,12,13,14]

# This will download the files if you don't have them yet,
# and then return the paths to the files.
physionet_paths = mne.datasets.eegbci.load_data(subject_id, event_codes)

# Load each of the files
parts = [mne.io.read_raw_edf(path, preload=True,stim_channel='auto', verbose='WARNING')
         for path in physionet_paths]

# Concatenate them
raw = concatenate_raws(parts)

# Find the events in this dataset
events, _ = mne.events_from_annotations(raw)

# Use only EEG channels
eeg_channel_inds = mne.pick_types(raw.info, meg=False, eeg=True, stim=False, eog=False,
                   exclude='bads')

# Extract trials, only using EEG channels
epoched = mne.Epochs(raw, events, dict(hands_or_left=2, feet_or_right=3), tmin=1, tmax=4.1, proj=False, picks=eeg_channel_inds,
                baseline=None, preload=True)

## Convert data to Braindecode format

Braindecode has a minimalistic ```SignalAndTarget``` class, with attributes `X` for the signal and `y` for the labels. `X` should have these dimensions: trials x channels x timesteps. `y` should have one label per trial.

In [4]:
import numpy as np
# Convert data from volt to millivolt
# Pytorch expects float32 for input and int64 for labels.
X = (epoched.get_data() * 1e6).astype(np.float32)
y = (epoched.events[:,2] - 2).astype(np.int64) #2,3 -> 0,1

We use the first 40 trials for training and the next 30 trials for validation. The validation accuracies can be used to tune hyperparameters such as learning rate etc. The final 20 trials are split apart so we have a final hold-out evaluation set that is not part of any hyperparameter optimization. As mentioned before, this dataset is dangerously small to get any meaningful results and only used here for quick demonstration purposes.

In [5]:
from braindecode.datautil.signal_target import SignalAndTarget

train_set = SignalAndTarget(X[:40], y=y[:40])
valid_set = SignalAndTarget(X[40:70], y=y[40:70])


## Create the model

Braindecode comes with some predefined convolutional neural network architectures for raw time-domain EEG. Here, we use the shallow ConvNet model from [Deep learning with convolutional neural networks for EEG decoding and visualization](https://arxiv.org/abs/1703.05051).

In [6]:
from braindecode.models.shallow_fbcsp import ShallowFBCSPNet
from torch import nn
from braindecode.torch_ext.util import set_random_seeds

# Set if you want to use GPU
# You can also use torch.cuda.is_available() to determine if cuda is available on your machine.
cuda = False
set_random_seeds(seed=20170629, cuda=cuda)
n_classes = 2
in_chans = train_set.X.shape[1]
# final_conv_length = auto ensures we only get a single output in the time dimension
model = ShallowFBCSPNet(in_chans=in_chans, n_classes=n_classes,
                        input_time_length=train_set.X.shape[2],
                        final_conv_length='auto')
if cuda:
    model.cuda()


We use [AdamW](https://arxiv.org/abs/1711.05101) to optimize the parameters of our network together with [Cosine Annealing](https://arxiv.org/abs/1608.03983) of the learning rate. We supply some default parameters that we have found to work well for motor decoding, however we strongly encourage you to perform your own hyperparameter optimization using cross validation on your training data.

<div class="alert alert-info">

We will now use the Braindecode model class directly to perform the training in a few lines of code. If you instead want to use your own training loop, have a look at the [Trialwise Low-Level Tutorial](./TrialWise_LowLevel.html).

</div>

In [7]:
from braindecode.torch_ext.optimizers import AdamW
import torch.nn.functional as F
#optimizer = AdamW(model.parameters(), lr=1*0.01, weight_decay=0.5*0.001) # these are good values for the deep model
optimizer = AdamW(model.parameters(), lr=0.0625 * 0.01, weight_decay=0)
model.compile(loss=F.nll_loss, optimizer=optimizer, iterator_seed=1,)

## Run the training

In [8]:
model.fit(train_set.X, train_set.y, epochs=30, batch_size=64, scheduler='cosine',
         validation_data=(valid_set.X, valid_set.y),)

2019-05-27 13:45:17,834 INFO : Run until first stop...
2019-05-27 13:45:18,483 INFO : Epoch 0
2019-05-27 13:45:18,485 INFO : train_loss                5.34665
2019-05-27 13:45:18,485 INFO : valid_loss                5.13145
2019-05-27 13:45:18,486 INFO : train_misclass            0.47500
2019-05-27 13:45:18,486 INFO : valid_misclass            0.46667
2019-05-27 13:45:18,487 INFO : runtime                   0.00000
2019-05-27 13:45:18,488 INFO : 
2019-05-27 13:45:19,574 INFO : Time only for training updates: 1.09s
2019-05-27 13:45:20,319 INFO : Epoch 1
2019-05-27 13:45:20,322 INFO : train_loss                1.18747
2019-05-27 13:45:20,324 INFO : valid_loss                1.44545
2019-05-27 13:45:20,325 INFO : train_misclass            0.45000
2019-05-27 13:45:20,327 INFO : valid_misclass            0.53333
2019-05-27 13:45:20,329 INFO : runtime                   1.74098
2019-05-27 13:45:20,330 INFO : 
2019-05-27 13:45:21,350 INFO : Time only for training updates: 1.02s
2019-05-27 13:4

2019-05-27 13:45:50,119 INFO : valid_misclass            0.16667
2019-05-27 13:45:50,121 INFO : runtime                   1.75996
2019-05-27 13:45:50,123 INFO : 
2019-05-27 13:45:51,134 INFO : Time only for training updates: 1.01s
2019-05-27 13:45:51,858 INFO : Epoch 18
2019-05-27 13:45:51,860 INFO : train_loss                0.03033
2019-05-27 13:45:51,862 INFO : valid_loss                0.50634
2019-05-27 13:45:51,864 INFO : train_misclass            0.00000
2019-05-27 13:45:51,865 INFO : valid_misclass            0.16667
2019-05-27 13:45:51,867 INFO : runtime                   1.74143
2019-05-27 13:45:51,869 INFO : 
2019-05-27 13:45:52,946 INFO : Time only for training updates: 1.08s
2019-05-27 13:45:53,671 INFO : Epoch 19
2019-05-27 13:45:53,674 INFO : train_loss                0.02815
2019-05-27 13:45:53,675 INFO : valid_loss                0.50780
2019-05-27 13:45:53,677 INFO : train_misclass            0.00000
2019-05-27 13:45:53,679 INFO : valid_misclass            0.16667
201

The monitored values are also stored into a pandas dataframe:

In [9]:
model.epochs_df

train_loss  valid_loss  train_misclass  valid_misclass   runtime
0     5.346649    5.131454           0.475        0.466667  0.000000
1     1.187472    1.445452           0.450        0.533333  1.740984
2     0.974734    1.217927           0.400        0.500000  1.777023
3     0.677576    0.901526           0.300        0.400000  1.748683
4     0.444574    0.676924           0.275        0.300000  1.755075
5     0.298528    0.551715           0.200        0.200000  1.771130
6     0.211601    0.507913           0.100        0.166667  2.211694
7     0.132909    0.469927           0.050        0.166667  2.728657
8     0.097908    0.452408           0.000        0.166667  1.762245
9     0.077446    0.453012           0.000        0.200000  1.841966
10    0.066468    0.459292           0.000        0.200000  1.813261
11    0.059477    0.472259           0.000        0.200000  1.749265
12    0.053263    0.487993           0.000        0.200000  1.757071
13    0.047088    0.504074           0.000        0.200000  1.747344
14    0.042468    0.508204           0.000        0.200000  1.875502
15    0.039186    0.512052           0.000        0.200000  1.756878
16    0.036201    0.512707           0.000        0.200000  1.763641
17    0.032971    0.507012           0.000        0.166667  1.759965
18    0.030331    0.506342           0.000        0.166667  1.741430
19    0.028149    0.507796           0.000        0.166667  1.811639
20    0.026143    0.511578           0.000        0.166667  1.744909
21    0.024460    0.515335           0.000        0.166667  1.744946
22    0.023193    0.518014           0.000        0.166667  1.746660
23    0.022102    0.520473           0.000        0.166667  1.778730
24    0.021306    0.523084           0.000        0.166667  1.789039
25    0.020703    0.524732           0.000        0.166667  1.745571
26    0.020286    0.525779           0.000        0.166667  1.749797
27    0.020023    0.525761           0.000        0.166667  1.764305
28    0.019861    0.525160           0.000        0.166667  1.739945
29    0.019783    0.524232           0.000        0.166667  1.762381
30    0.019764    0.523157           0.000        0.166667  1.761538

Eventually, we arrive at 83.4% accuracy, so 25 from 30 trials are correctly predicted. In the [Cropped Decoding Tutorial](./Cropped_Decoding.html), we can learn how to achieve higher accuracies using cropped training.

## Evaluation

Once we have all our hyperparameters and architectural choices done, we can evaluate the accuracies to report in our publication by evaluating on the test set:

In [10]:
test_set = SignalAndTarget(X[70:], y=y[70:])

model.evaluate(test_set.X, test_set.y)

{'loss': 0.43049120903015137,
 'misclass': 0.19999999999999996,
 'runtime': 0.00031256675720214844}

We can also retrieve predicted labels per trial as such:

In [11]:
model.predict_classes(test_set.X)

array([1, 0, 1, 0, 0, 0, 1, 0, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 0])

We can also retrieve the raw network outputs per trial as such:

<div class="alert alert-warning">
Note these are log-softmax outputs, so to get probabilities one would have to exponentiate them using `th.exp`.
</div>

In [12]:
model.predict_outs(test_set.X)

array([[-3.108049  , -0.0457173 ],
       [-0.18737975, -1.7668451 ],
       [-3.550216  , -0.02913891],
       [-0.00889281, -4.7269597 ],
       [-0.03029956, -3.5117326 ],
       [-0.00847233, -4.775178  ],
       [-4.006974  , -0.01835574],
       [-0.4073605 , -1.0948324 ],
       [-0.02217731, -3.819753  ],
       [-0.22672828, -1.5952262 ],
       [-3.5868406 , -0.02807612],
       [-1.3834822 , -0.28862125],
       [-0.32644472, -1.2782807 ],
       [-1.3229265 , -0.30972955],
       [-0.08954818, -2.4574184 ],
       [-0.0186951 , -3.9888284 ],
       [-0.09142652, -2.4375842 ],
       [-0.24392553, -1.5303771 ],
       [-0.03591001, -3.3446407 ],
       [-0.16686489, -1.8728433 ]], dtype=float32)

<div class="alert alert-info">

If you want to try cross-subject decoding, changing the loading code to the following will perform cross-subject decoding on imagined left vs right hand closing, with 50 training and 5 validation subjects (Warning, might be very slow if you are on CPU):

</div>

In [ ]:
import mne
import numpy as np
from mne.io import concatenate_raws
from braindecode.datautil.signal_target import SignalAndTarget

# First 50 subjects as train
physionet_paths = [ mne.datasets.eegbci.load_data(sub_id,[4,8,12,]) for sub_id in range(1,51)]
physionet_paths = np.concatenate(physionet_paths)
parts = [mne.io.read_raw_edf(path, preload=True,stim_channel='auto')
         for path in physionet_paths] 

raw = concatenate_raws(parts)

picks = mne.pick_types(raw.info, meg=False, eeg=True, stim=False, eog=False,
                   exclude='bads')

# Find the events in this dataset
events, _ = mne.events_from_annotations(raw)

# Read epochs (train will be done only between 1 and 2s)
# Testing will be done with a running classifier
epoched = mne.Epochs(raw, events, dict(hands=2, feet=3), tmin=1, tmax=4.1, proj=False, picks=picks,
                baseline=None, preload=True)

# 51-55 as validation subjects
physionet_paths_valid = [mne.datasets.eegbci.load_data(sub_id,[4,8,12,]) for sub_id in range(51,56)]
physionet_paths_valid = np.concatenate(physionet_paths_valid)
parts_valid = [mne.io.read_raw_edf(path, preload=True,stim_channel='auto')
         for path in physionet_paths_valid]
raw_valid = concatenate_raws(parts_valid)

picks_valid = mne.pick_types(raw_valid.info, meg=False, eeg=True, stim=False, eog=False,
                   exclude='bads')

events_valid = mne.find_events(raw_valid, shortest_event=0, stim_channel='STI 014')

# Read epochs (train will be done only between 1 and 2s)
# Testing will be done with a running classifier
epoched_valid = mne.Epochs(raw_valid, events_valid, dict(hands=2, feet=3), tmin=1, tmax=4.1, proj=False, picks=picks_valid,
                baseline=None, preload=True)

train_X = (epoched.get_data() * 1e6).astype(np.float32)
train_y = (epoched.events[:,2] - 2).astype(np.int64) #2,3 -> 0,1
valid_X = (epoched_valid.get_data() * 1e6).astype(np.float32)
valid_y = (epoched_valid.events[:,2] - 2).astype(np.int64) #2,3 -> 0,1
train_set = SignalAndTarget(train_X, y=train_y)
valid_set = SignalAndTarget(valid_X, y=valid_y)

## Dataset references


 This dataset was created and contributed to PhysioNet by the developers of the [BCI2000](http://www.schalklab.org/research/bci2000) instrumentation system, which they used in making these recordings. The system is described in:
 
     Schalk, G., McFarland, D.J., Hinterberger, T., Birbaumer, N., Wolpaw, J.R. (2004) BCI2000: A General-Purpose Brain-Computer Interface (BCI) System. IEEE TBME 51(6):1034-1043.

[PhysioBank](https://physionet.org/physiobank/) is a large and growing archive of well-characterized digital recordings of physiologic signals and related data for use by the biomedical research community and further described in:

    Goldberger AL, Amaral LAN, Glass L, Hausdorff JM, Ivanov PCh, Mark RG, Mietus JE, Moody GB, Peng C-K, Stanley HE. (2000) PhysioBank, PhysioToolkit, and PhysioNet: Components of a New Research Resource for Complex Physiologic Signals. Circulation 101(23):e215-e220.